### Generar tonos simples con numpy y reproducir con sounddevice
Esta opción es útil si quieres generar ondas sonoras básicas como senoidales, cuadradas, etc.

In [1]:
import numpy as np
import sounddevice as sd


In [2]:
def generate_tone(frequency, duration, sample_rate=44100):
    """
    Genera un tono senoidal.
    frequency: Frecuencia del tono en Hz.
    duration: Duración en segundos.
    sample_rate: Frecuencia de muestreo.
    """
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    tone = 0.5 * np.sin(2 * np.pi * frequency * t)  # Amplitud de 0.5 para evitar distorsión
    return tone

In [3]:
# Genera un tono de 440 Hz (nota La) durante 2 segundos
tone = generate_tone(frequency=440, duration=2)
sd.play(tone, samplerate=44100)  # Reproduce el tono
sd.wait()  # Espera hasta que termine

### Crear un archivo WAV con wave

In [4]:
import wave

In [5]:
def generate_tone_wav(frequency, duration, sample_rate=44100, file_name="tone.wav"):
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    tone = (0.5 * np.sin(2 * np.pi * frequency * t) * 32767).astype(np.int16)  # Escalado a 16 bits
    with wave.open(file_name, 'w') as wav_file:
        wav_file.setnchannels(1)  # Mono
        wav_file.setsampwidth(2)  # 16 bits por muestra
        wav_file.setframerate(sample_rate)
        wav_file.writeframes(tone.tobytes())

In [13]:
generate_tone_wav(frequency=700, duration=2, file_name="data/audios_generados/output.wav")


In [14]:
import IPython.display as ipd

audio_file = 'data/audios_generados/output.wav'

ipd.Audio(audio_file) 

### Crear audios con soundfile

In [16]:
import soundfile as sf

def save_tone_with_soundfile(frequency, duration, file_name="tone.wav", sample_rate=44100):
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    tone = 0.5 * np.sin(2 * np.pi * frequency * t)  # Amplitud de 0.5
    sf.write(file_name, tone, samplerate=sample_rate)

# Guarda un tono de 440 Hz
save_tone_with_soundfile(frequency=440, duration=2, file_name="data/audios_generados/output2.wav")


In [17]:
audio_file = 'data/audios_generados/output2.wav'
ipd.Audio(audio_file)

### GENERAR un acorde

In [18]:
def generate_chord(frequencies, duration, file_name="chord.wav", sample_rate=44100):
    '''
    genera un acorde a partir de varias frecuencias.
    frequencies: lista de frecuencias en hz.
    sample_rate: ffrecuencia de muestreo.
    '''
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    chord = sum(0.5 * np.sin(2 * np.pi * freq * t) for freq in frequencies)
    chord /= len(frequencies)  
    sf.write(file_name, chord, samplerate=sample_rate)

In [20]:
# Genera un acorde mayor (Do, Mi, Sol)
generate_chord(frequencies=[261.63, 329.63, 392.00], duration=2, file_name="data/audios_generados/chord.wav")

In [21]:
file_name="data/audios_generados/chord.wav"
ipd.Audio(file_name)

In [22]:
generate_chord(frequencies=[261.63, 311.13, 392.00], duration=2, file_name="data/audios_generados/do_menor.wav")


In [23]:
do_menor="data/audios_generados/do_menor.wav"
ipd.Audio(do_menor)

In [26]:
def generate_fm_tone(carrier_freq, mod_freq, mod_index, duration, file_name="fm_tone.wav", sample_rate=44100):
    """
    Genera un tono con modulación de frecuencia (FM Synthesis).
    carrier_freq: Frecuencia portadora.
    mod_freq: Frecuencia moduladora.
    mod_index: Índice de modulación.
    duration: Duración en segundos.
    """
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    modulator = mod_index * np.sin(2 * np.pi * mod_freq * t)  # Onda moduladora
    fm_tone = 0.5 * np.sin(2 * np.pi * carrier_freq * t + modulator)  # FM Synthesis
    sf.write(file_name, fm_tone, samplerate=sample_rate)


In [ ]:
# Genera un tono FM
generate_fm_tone(carrier_freq=440, mod_freq=50, mod_index=75, duration=2, file_name="data/audios_generados/fm_tone.wav")


In [30]:
file_name="data/audios_generados/fm_tone.wav"
ipd.Audio(file_name)

In [28]:
def generate_tone_with_adsr(frequency, duration, adsr, file_name="adsr_tone.wav", sample_rate=44100):
    """
    Genera un tono con envolvente ADSR.
    frequency: Frecuencia del tono.
    duration: Duración en segundos.
    adsr: Diccionario con las fases de la envolvente (Attack, Decay, Sustain, Release).
    """
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    tone = 0.5 * np.sin(2 * np.pi * frequency * t)
    
    # Genera la envolvente ADSR
    attack_time, decay_time, sustain_level, release_time = adsr.values()
    attack_samples = int(attack_time * sample_rate)
    decay_samples = int(decay_time * sample_rate)
    release_samples = int(release_time * sample_rate)
    sustain_samples = len(t) - (attack_samples + decay_samples + release_samples)
    
    envelope = np.concatenate([
        np.linspace(0, 1, attack_samples),  # Attack
        np.linspace(1, sustain_level, decay_samples),  # Decay
        np.full(sustain_samples, sustain_level),  # Sustain
        np.linspace(sustain_level, 0, release_samples)  # Release
    ])
    
    # Aplica la envolvente al tono
    adsr_tone = tone[:len(envelope)] * envelope
    sf.write(file_name, adsr_tone, samplerate=sample_rate)


In [29]:

# Genera un tono con envolvente ADSR
generate_tone_with_adsr(
    frequency=440,
    duration=2,
    adsr={"Attack": 0.1, "Decay": 0.1, "Sustain": 0.7, "Release": 0.2},
    file_name="data/audios_generados/adsr_tone.wav"
)


In [31]:
file_name="data/audios_generados/adsr_tone.wav"
ipd.Audio(file_name)

### pianito

In [37]:
def generate_note(frequency, duration, sample_rate=44100, amplitude=0.5):
    """
    Genera una onda senoidal para una nota específica.
    frequency: Frecuencia de la nota (Hz).
    duration: Duración de la nota (segundos).
    sample_rate: Frecuencia de muestreo.
    amplitude: Amplitud del sonido.
    """
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    return amplitude * np.sin(2 * np.pi * frequency * t)

def generate_melody(notes, durations, file_name="melody.wav", sample_rate=44100):
    """
    Genera una sucesión de notas (melodía).
    notes: Lista de frecuencias de las notas (Hz).
    durations: Lista de duraciones de las notas (segundos).
    file_name: Nombre del archivo de salida.
    sample_rate: Frecuencia de muestreo.
    """
    melody = np.array([])

    for freq, dur in zip(notes, durations):
        note = generate_note(freq, dur, sample_rate)
        melody = np.concatenate((melody, note))  # Concatenar notas

    # Normaliza la amplitud final
    melody /= np.max(np.abs(melody))

    # Guarda la melodía como archivo WAV
    sf.write(file_name, melody, samplerate=sample_rate)



In [38]:
# Frecuencias en Hz de las notas: Do, Re, Mi, Fa, Sol, La, Si, Do (C4-B4)
notes = [261.63, 293.66, 329.63, 349.23, 392.00, 440.00, 493.88, 523.25]
durations = [0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 1.0]  # Duración de cada nota en segundos

# Genera la melodía
generate_melody(notes, durations, file_name="data/audios_generados/melody.wav")


In [39]:
melodia ="data/audios_generados/melody.wav"
ipd.Audio(melodia)

pruebita aplicable a la mierda de librosa

In [40]:
import numpy as np
import pandas as pd
import soundfile as sf

def generate_audio_from_features(row, sample_rate=44100):
    """
    Genera un audio basado en una fila del dataset.
    row: Fila del dataset con las características de la pista.
    sample_rate: Frecuencia de muestreo.
    """
    duration = row['duration']  # Duración del audio
    rms_energy = row['rms_energy']  # Energía RMS como amplitud
    tempo = row['tempo']  # Tempo en BPM
    spectral_centroid = row['spectral_centroid']  # Brillo del sonido
    mfccs = [row[f'mfcc_{i}'] for i in range(1, 14)]  # Los 13 MFCCs

    # Genera el tiempo para la duración
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)

    # Genera una onda senoidal básica modulada por los MFCCs
    base_freq = spectral_centroid / 10  # Escala el centroid como frecuencia base
    tone = rms_energy * np.sin(2 * np.pi * base_freq * t)

    # Aplica una modulación basada en los MFCCs
    for i, mfcc in enumerate(mfccs):
        mod_freq = base_freq + mfcc
        tone += 0.1 * np.sin(2 * np.pi * mod_freq * t)

    # Normaliza el audio
    tone /= np.max(np.abs(tone))

    return tone



In [43]:
df = pd.read_csv("data/audio_features.csv")
df


file_name    duration  rms_energy       tempo  zero_crossing_rate  \
0             2   45.060998    0.105231  139.674831            0.036522   
1             3   45.034875    0.116200   95.703125            0.013482   
2             4   45.034875    0.184904   84.720799            0.037387   
3             5   45.034875    0.149748  123.046875            0.036256   
4             7   45.060998    0.267147  120.185320            0.012908   
...         ...         ...         ...         ...                 ...   
1797       2054   95.555918    0.113068  184.570312            0.014080   
1798       2055  283.846531    0.162186  123.046875            0.075789   
1799       2056  167.993469    0.082061   99.384014            0.032717   
1800       2057  183.013878    0.174957  126.048018            0.064016   
1801       2058  274.285714    0.137872  109.956782            0.045160   

      spectral_centroid  spectral_bandwidth  spectral_rolloff     mfcc_1  \
0           1894.684236         2486.199436       3912.602977 -200.25986   
1           1043.167353         1909.448198       2180.582380 -285.92618   
2           1917.091287         2596.755681       3948.575488 -163.72380   
3           1898.303391         2731.843915       3771.885536 -190.34114   
4           1269.457957         2229.921617       2820.644373 -208.91113   
...                 ...                 ...               ...        ...   
1797         609.154432         1049.450390        951.290923 -345.00327   
1798        3022.224838         3079.615902       6087.714573 -158.86028   
1799        1718.402948         2496.094006       3180.802323 -275.03820   
1800        2849.405262         3230.593970       5976.757444 -117.86253   
1801        2014.296254         2475.900249       4147.859455 -189.12662   

         mfcc_2  ...     mfcc_4     mfcc_5     mfcc_6     mfcc_7     mfcc_8  \
0     171.77261  ...  36.403446   0.236144  17.683105   1.365153   9.277338   
1     159.13257  ...  33.757630  25.207740  20.010067  18.247145  21.900534   
2     166.30011  ...  36.676277  10.505774  39.914690  -2.767269   7.671440   
3     162.43484  ...  38.936256  -6.951975  10.322243 -25.887856   6.754761   
4     156.98831  ...  62.610767  13.259298  27.919954  20.397331  12.311554   
...         ...  ...        ...        ...        ...        ...        ...   
1797  170.27849  ...  29.274414  42.960830  13.713198   7.100956   9.439139   
1798  125.53489  ...  49.987500  -8.285833  20.021326 -10.491330   9.692228   
1799  162.40372  ...  31.144010   8.626746   3.782925   5.743162   7.962147   
1800  144.67566  ...  52.916336  -2.505956  30.558453 -15.577179  18.441471   
1801  164.13486  ...  35.155888   9.586875  25.527956  -4.991922  10.019704   

         mfcc_9    mfcc_10   mfcc_11    mfcc_12   mfcc_13  
0      1.370861  -3.264254  6.485454   1.080217 -1.031337  
1     11.854753  10.960750  9.535206   7.900679  2.072755  
2     -2.185159   2.389242 -0.667877   0.583180  0.228795  
3    -14.676446  -6.158040 -7.251907 -13.481309 -1.855042  
4     10.173452   2.516552  0.894844  -1.296418  3.176229  
...         ...        ...       ...        ...       ...  
1797  -5.665821  -8.279132 -1.064172  -3.373265 -2.839869  
1798  -1.173238   4.142817 -2.555365   8.149619  2.640244  
1799  -0.317671   4.725707 -5.704327   1.246315 -1.315412  
1800  -5.380016   9.218659 -0.420411  -0.137583 -5.812217  
1801  -3.723221   1.341275 -3.279121   0.563044  0.733538  

[1802 rows x 21 columns]

In [44]:
row = df.iloc[0]  # Cambia 0 por el índice de la fila deseada

audio_row = generate_audio_from_features(row)

# Guarda el audio generado en un archivo
sf.write("audio_file_2.wav", audio_row, samplerate=44100)



In [45]:
pruebita_extraña ='audio_file_2.wav'
ipd.Audio(pruebita_extraña)

vaya basura

## practica

después de varios intentos y pruebas de la librería y ver como funciona vamos a tratar de generar una melodu¡ía más compleja donde de superponvas distintas melodias

In [46]:
def generate_note(frequency, duration, amplitude=0.5, sample_rate=44100):

    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    return amplitude * np.sin(2 * np.pi * frequency * t)

def generate_voice(notes, durations, amplitudes, sample_rate=44100):

    voice = np.array([])
    for freq, dur, amp in zip(notes, durations, amplitudes):
        note = generate_note(freq, dur, amplitude=amp, sample_rate=sample_rate)
        voice = np.concatenate((voice, note))
    return voice

def mix_voices(voices):

    max_len = max(len(voice) for voice in voices)
    mixed = np.zeros(max_len)
    for voice in voices:
        mixed[:len(voice)] += voice  
    mixed /= len(voices)  
    return mixed



In [49]:
#le pedimos a chatgpt que nos de una ejemplo e uso para nuestra funci´n
# Definir melodías (frecuencias y duraciones) para tres voces
voice_1_notes = [261.63, 329.63, 392.00, 440.00]  # Do, Mi, Sol, La
voice_2_notes = [392.00, 440.00, 493.88, 523.25]  # Sol, La, Si, Do
voice_3_notes = [261.63, 293.66, 329.63, 349.23]  # Do, Re, Mi, Fa

durations = [1, 1, 1, 1]  # Todas las notas duran 1 segundo
amplitudes = [0.7, 0.8, 0.5, 0.3]  # Amplitudes constantes

# Generar cada voz
voice_1 = generate_voice(voice_1_notes, durations, amplitudes)
voice_2 = generate_voice(voice_2_notes, durations, amplitudes)
voice_3 = generate_voice(voice_3_notes, durations, amplitudes)

# Mezclar las voces
final_audio = mix_voices([voice_1, voice_2, voice_3])

# Guardar el audio final
sf.write("complex_melody.wav", final_audio, samplerate=44100)


In [50]:
mamaheuvo ='complex_melody.wav'
ipd.Audio(mamaheuvo)